### Stage 1 - Image captioning and design prompt

In [1]:
import os
import json
import torch
from transformers import Blip2Processor, Blip2ForConditionalGeneration

/home/joung/r12725056/myenv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-12-03 20:55:39.111518: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-12-03 20:55:39.119010: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1733230539.128361  112290 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1733230539.131159  112290 cuda_blas.cc:1418] Un

#### Model 1 - blip2-opt-2.7b

In [ ]:
# Load the processor1 and model
processor1 = Blip2Processor.from_pretrained("Salesforce/blip2-opt-2.7b")
model1 = Blip2ForConditionalGeneration.from_pretrained(
    "Salesforce/blip2-opt-2.7b", torch_dtype=torch.float16
)

# Move the model to GPU if available
device = "cuda" if torch.cuda.is_available() else "cpu"
model1.to(device)
print(f"Running on {device}")

Loading checkpoint shards: 100%|██████████| 2/2 [00:01<00:00,  1.80it/s]


Running on cuda


In [ ]:
from PIL import Image

def generate_caption(image_path, model):
    # Open and process the image
    image = Image.open(image_path).convert("RGB")
    prompt = "Caption in English:"
    inputs = processor1(images=image, text=prompt, return_tensors="pt").to(device, torch.float16)
    
    # Generate caption
    generated_ids = model.generate(**inputs, max_new_tokens=50)
    caption = processor1.decode(generated_ids[0], skip_special_tokens=True)
    
    return caption

In [ ]:
# Path to your dataset 
image_folder = "images"
label_json_path = "label.json"

# Load the label.json file
with open(label_json_path, "r") as f:
    label_data = json.load(f)

# Dictionary to store image data
image_data_dict = {}

# idx = 0
# Iterate through images and generate captions
for image_file in os.listdir(image_folder):
    print(f"Processing {image_file}")
    # idx += 1
    if image_file.lower().endswith(('.png', '.jpg', '.jpeg')):
        label_info = next((item for item in label_data if item["image"] == image_file), None)
        if label_info:
            labels = label_info.get("labels", [])
            height = label_info.get("height", None)
            width = label_info.get("width", None)
            bboxes = label_info.get("bboxes", [])

            image_path = os.path.join(image_folder, image_file)
            caption = generate_caption(image_path, model1)
            prompt_w_label = f"{caption} {', '.join(labels)}, height: {height}, width: {width}"
            prompt_w_suffix = f"{prompt_w_label}, HD quality, detailed"

        
            image_data = {
                "image": image_file,
                "labels": labels,
                "height": height,
                "width": width,
                "bboxes": bboxes,
                "generated_text": caption,
                "prompt_w_label": prompt_w_label,
                "prompt_w_suffix": prompt_w_suffix
            }

            # Store the combined data
            image_data_dict[image_file] = image_data

            print(f"Processed {image_file}: {image_data}")
        # if idx > 10:
        #     break

# Save the combined data to a JSON file
with open("image_data_blip2-opt-2.7b.json", "w") as f:
    json.dump(image_data_dict, f, indent=4)

Processing pexels-photo-4219658.jpeg
Processed pexels-photo-4219658.jpeg: {'image': 'pexels-photo-4219658.jpeg', 'labels': ['Tools', 'Tools', 'Tools', 'Tools', 'Tools', 'Tools', 'Hands', 'Hands', 'Hands', 'Hands', 'Person', 'Person'], 'height': 512, 'width': 512, 'bboxes': [[186.81881600000003, 287.08582399999995, 242.97139200000004, 326.85747200000003], [439.237888, 169.028352, 499.19974400000007, 251.542784], [462.323712, 178.62860799999999, 485.1046400000001, 226.40025599999998], [414.55232000000007, 71.542784, 444.418816, 79.08556800000001], [252.11417600000001, 33.371648, 294.171392, 79.885824], [364.26649599999996, 240.80025599999996, 410.971136, 256.800256], [417.75232000000005, 279.771392, 511.9997440000001, 434.05696], [309.4092800000001, 210.171648, 370.74278400000003, 316.457216], [117.714432, 93.142528, 188.87628800000002, 183.65696], [72.38092800000001, 0.000256000000000256, 115.88556799999999, 33.257216], [274.209536, 205.48556799999997, 512.0002560000001, 504.0], [0.0, 0

#### Model 2 - blip2-opt-6.7b

In [ ]:
# Load the processor and model
processor2 = Blip2Processor.from_pretrained("Salesforce/blip2-opt-6.7b")
model2 = Blip2ForConditionalGeneration.from_pretrained(
    "Salesforce/blip2-opt-6.7b", torch_dtype=torch.float16
)

# Move the model2 to GPU if available
device = "cuda" if torch.cuda.is_available() else "cpu"
model2.to(device)
print(f"Running on {device}")

In [ ]:
# Path to your dataset 
image_folder = "images"
label_json_path = "label.json"

# Load the label.json file
with open(label_json_path, "r") as f:
    label_data = json.load(f)

# Dictionary to store image data
image_data_dict = {}

# idx = 0
# Iterate through images and generate captions
for image_file in os.listdir(image_folder):
    print(f"Processing {image_file}")
    # idx += 1
    if image_file.lower().endswith(('.png', '.jpg', '.jpeg')):
        label_info = next((item for item in label_data if item["image"] == image_file), None)
        if label_info:
            labels = label_info.get("labels", [])
            height = label_info.get("height", None)
            width = label_info.get("width", None)
            bboxes = label_info.get("bboxes", [])

            image_path = os.path.join(image_folder, image_file)
            caption = generate_caption(image_path, model2)
            prompt_w_label = f"{caption} {', '.join(labels)}, height: {height}, width: {width}"
            prompt_w_suffix = f"{prompt_w_label}, HD quality, detailed"

        
            image_data = {
                "image": image_file,
                "labels": labels,
                "height": height,
                "width": width,
                "bboxes": bboxes,
                "generated_text": caption,
                "prompt_w_label": prompt_w_label,
                "prompt_w_suffix": prompt_w_suffix
            }

            # Store the combined data
            image_data_dict[image_file] = image_data

            print(f"Processed {image_file}: {image_data}")
        # if idx > 10:
        #     break

# Save the combined data to a JSON file
with open("image_data_blip2-opt-6.7b.json", "w") as f:
    json.dump(image_data_dict, f, indent=4)

### Stage 2 - Text to image

In [2]:
import os
import json
from diffusers import StableDiffusionPipeline

# Load the Stable Diffusion model
pipe = StableDiffusionPipeline.from_pretrained(
    "runwayml/stable-diffusion-v1-5", torch_dtype=torch.float16
)

# Move the model to GPU if available
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Running on {device}")

pipe.to(device)
pipe.enable_attention_slicing()

Loading pipeline components...: 100%|██████████| 7/7 [00:00<00:00,  8.25it/s]


Running on cuda


In [3]:
def generate_augmented_image(prompt, output_path):
    # Generate the image
    generated_image = pipe(prompt).images[0]
    # Save the generated image
    generated_image.save(output_path)

#### 2.7b Suffix to image

In [13]:
# Load the JSON data generated in Stage 1
with open("image_data_blip2-opt-2.7b.json", "r") as f:
    enhanced_data = json.load(f)

# Directory to save augmented images
augmented_images_dir = "augmented_images_suffix"
os.makedirs(augmented_images_dir, exist_ok=True)

# Iterate through data and generate augmented images
for image_file, image_info in enhanced_data.items():
    caption = image_info["prompt_w_suffix"]  # Use the suffix-enhanced prompt
    output_image_path = os.path.join(augmented_images_dir, f"{image_file}")
    
    # Generate the augmented image
    generate_augmented_image(prompt=caption, output_path=output_image_path)
    print(f"Generated augmented image for {image_file} at {output_image_path}")

100%|██████████| 50/50 [00:03<00:00, 16.29it/s]


Generated augmented image for pexels-photo-4219658.jpeg at augmented_images_suffix/pexels-photo-4219658.jpeg


100%|██████████| 50/50 [00:02<00:00, 16.80it/s]


Generated augmented image for pexels-photo-5920626.jpeg at augmented_images_suffix/pexels-photo-5920626.jpeg


100%|██████████| 50/50 [00:02<00:00, 16.76it/s]


...

Generated augmented image for pexels-photo-8205058.jpeg at augmented_images_suffix/pexels-photo-8205058.jpeg


100%|██████████| 50/50 [00:03<00:00, 16.53it/s]


Generated augmented image for pexels-photo-9301898.jpeg at augmented_images_suffix/pexels-photo-9301898.jpeg


100%|██████████| 50/50 [00:03<00:00, 16.53it/s]


Generated augmented image for pexels-photo-4480798.jpeg at augmented_images_suffix/pexels-photo-4480798.jpeg


In [1]:
from PIL import Image
import os

def resize_images(input_folder, output_folder, size=(512, 512)):
    os.makedirs(output_folder, exist_ok=True)
    for file in os.listdir(input_folder):
        if file.endswith(('jpg', 'jpeg', 'png')):
            img = Image.open(os.path.join(input_folder, file)).convert('RGB')
            img = img.resize(size)
            img.save(os.path.join(output_folder, file))
    print(f"Resized images saved to {output_folder}")

In [ ]:
resize_images("augmented_images_suffix", "resized_images_suffix")
resize_images("images", "resized_images")
# python -m pytorch_fid resized_images_suffix resized_images
# FID:  51.06119518678611

#### 2.7b text(prompt) to image

In [5]:
# Load the JSON data generated in Stage 1
with open("image_data_blip2-opt-2.7b.json", "r") as f:
    enhanced_data = json.load(f)

# Directory to save augmented images
augmented_images_dir = "augmented_images_text"
os.makedirs(augmented_images_dir, exist_ok=True)

# Iterate through data and generate augmented images
for image_file, image_info in enhanced_data.items():
    caption = image_info["generated_text"]  # Use the suffix-enhanced prompt
    output_image_path = os.path.join(augmented_images_dir, f"{image_file}")
    
    # Generate the augmented image
    generate_augmented_image(prompt=caption, output_path=output_image_path)
    print(f"Generated augmented image for {image_file} at {output_image_path}")

100%|██████████| 50/50 [00:03<00:00, 16.48it/s]


Generated augmented image for pexels-photo-4219658.jpeg at augmented_images_text/pexels-photo-4219658.jpeg


100%|██████████| 50/50 [00:02<00:00, 16.82it/s]


Generated augmented image for pexels-photo-5920626.jpeg at augmented_images_text/pexels-photo-5920626.jpeg


100%|██████████| 50/50 [00:02<00:00, 16.82it/s]


...

Generated augmented image for pexels-photo-8205058.jpeg at augmented_images_text/pexels-photo-8205058.jpeg


100%|██████████| 50/50 [00:03<00:00, 16.48it/s]


Generated augmented image for pexels-photo-9301898.jpeg at augmented_images_text/pexels-photo-9301898.jpeg


100%|██████████| 50/50 [00:03<00:00, 16.51it/s]


Generated augmented image for pexels-photo-4480798.jpeg at augmented_images_text/pexels-photo-4480798.jpeg


In [ ]:
resize_images("augmented_images_text", "resized_images_text")
# python -m pytorch_fid resized_images_text resized_images
# FID:  46.09627004888341

Resized images saved to resized_images_text


#### Gligen - suffix + layout to image 

In [3]:
import torch
from diffusers import StableDiffusionGLIGENPipeline

pipe = StableDiffusionGLIGENPipeline.from_pretrained(
    "masterful/gligen-1-4-inpainting-text-box", variant="fp16", torch_dtype=torch.float16
)
pipe = pipe.to("cuda")

Loading pipeline components...:  29%|██▊       | 2/7 [00:00<00:00,  8.69it/s]/home/joung/r12725056/myenv/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
An error occurred while trying to fetch /home/joung/.cache/huggingface/hub/models--masterful--gligen-1-4-inpainting-text-box/snapshots/d6d957f8d27c40889c0d570a616571a5645c8be3/unet: Error no file named diffusion_pytorch_model.fp16.safetensors found in directory /home/joung/.cache/huggingface/hub/models--masterful--gligen-1-4-inpainting-text-box/snapshots/d6d957f8d27c40889c0d570a616571a5645c8be3/unet.
Defaulting to unsafe serialization. Pass `allow_pickle=False` to raise an error instead.
Loading pipeline components...:  71%|███████▏  | 5/7 [00:01<00:00,  4.64it/s]An error occurred while trying to fetch /home/joung/.cache/huggingface/hub

In [4]:
def normalize_bbox(bbox, img_width, img_height):
    x_min, y_min, x_max, y_max = bbox
    return [
        x_min / img_width,
        y_min / img_height,
        x_max / img_width,
        y_max / img_height,
    ]

In [9]:
import os
import json
from PIL import Image

# Load the JSON data generated in Stage 1
with open("image_data_blip2-opt-2.7b.json", "r") as f:
    enhanced_data = json.load(f)

output_dir = "./augmented_images_gligen"
os.makedirs(output_dir, exist_ok=True)

for image_name, attributes in enhanced_data.items():
    prompt = attributes["prompt_w_suffix"].strip()
    bboxes = attributes["bboxes"]
    labels = attributes["labels"]
    img_width = attributes["width"]
    img_height = attributes["height"]

    # Normalize bounding boxes
    normalized_bboxes = [normalize_bbox(bbox, img_width, img_height) for bbox in bboxes]
    input_image = Image.open(f"images/{image_name}").convert("RGB")

    # Generate the image
    images = pipe(
        prompt=prompt,
        gligen_phrases=labels,
        gligen_inpaint_image=input_image,
        gligen_boxes=normalized_bboxes,
        gligen_scheduled_sampling_beta=1,
        output_type="pil",
        num_inference_steps=50,
    ).images

    # Save the generated image
    output_path = os.path.join(output_dir, image_name)
    images[0].save(output_path)

100%|██████████| 50/50 [00:03<00:00, 16.10it/s]
Token indices sequence length is longer than the specified maximum sequence length for this model (132 > 77). Running this sequence through the model will result in indexing errors
The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: [', tools , tools , tools , tools , shoes , shoes , shoes , shoes , foot , foot , foot , foot , gloves , gloves , gloves , person , person , person , person , height : 5 1 2 , width : 5 1 2 , hd quality , detailed']
/home/joung/r12725056/myenv/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion_gligen/pipeline_stable_diffusion_gligen.py:704: FutureWarning: More that 30 objects found. Only first 30 objects will be processed.
  warnings.warn(
100%|██████████| 50/50 [00:03<00:00, 16.01it/s]
The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: [', detailed']
100%|██████████| 50/50 [00:03<00:00, 16.00i

In [ ]:
resize_images("augmented_images_gligen", "resized_images_gligen")
# FID:  32.20735526588726

Resized images saved to resized_images_gligen


### Generate 200 images for final 

In [1]:
import os
import json
import torch
from transformers import Blip2Processor, Blip2ForConditionalGeneration

/home/joung/r12725056/myenv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-12-05 14:46:48.404279: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-12-05 14:46:48.411655: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1733381208.420873  121658 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1733381208.423628  121658 cuda_blas.cc:1418] Un

In [2]:
# Load the processor1 and model
processor1 = Blip2Processor.from_pretrained("Salesforce/blip2-opt-2.7b")
model1 = Blip2ForConditionalGeneration.from_pretrained(
    "Salesforce/blip2-opt-2.7b", torch_dtype=torch.float16
)

# Move the model to GPU if available
device = "cuda" if torch.cuda.is_available() else "cpu"
model1.to(device)
print(f"Running on {device}")

Loading checkpoint shards: 100%|██████████| 2/2 [00:03<00:00,  1.92s/it]


Running on cuda


In [3]:
from PIL import Image

def generate_caption(image_path, model):
    # Open and process the image
    image = Image.open(image_path).convert("RGB")
    prompt = "Caption in English:"
    inputs = processor1(images=image, text=prompt, return_tensors="pt").to(device, torch.float16)
    
    # Generate caption
    generated_ids = model.generate(**inputs, max_new_tokens=50)
    caption = processor1.decode(generated_ids[0], skip_special_tokens=True)
    
    return caption

In [4]:
# Path to your dataset 
image_folder = "images"
label_json_path = "visualiztion_200.json"

# Load the label.json file
with open(label_json_path, "r") as f:
    label_data = json.load(f)

# Dictionary to store image data
image_data_dict = {}

# idx = 0
# Iterate through images and generate captions
for image_file in os.listdir(image_folder):
    print(f"Processing {image_file}")
    # idx += 1
    if image_file.lower().endswith(('.png', '.jpg', '.jpeg')):
        label_info = next((item for item in label_data if item["image"] == image_file), None)
        if label_info:
            labels = label_info.get("labels", [])
            height = label_info.get("height", None)
            width = label_info.get("width", None)
            bboxes = label_info.get("bboxes", [])

            image_path = os.path.join(image_folder, image_file)
            caption = generate_caption(image_path, model1)
            prompt_w_label = f"{caption} {', '.join(labels)}, height: {height}, width: {width}"
            prompt_w_suffix = f"{prompt_w_label}, HD quality, detailed"

        
            image_data = {
                "image": image_file,
                "labels": labels,
                "height": height,
                "width": width,
                "bboxes": bboxes,
                "generated_text": caption,
                "prompt_w_label": prompt_w_label,
                "prompt_w_suffix": prompt_w_suffix
            }

            # Store the combined data
            image_data_dict[image_file] = image_data

            print(f"Processed {image_file}: {image_data}")
        # if idx > 10:
        #     break

# Save the combined data to a JSON file
with open("image_data_blip2-opt-2.7b_200.json", "w") as f:
    json.dump(image_data_dict, f, indent=4)

Processing pexels-photo-4219658.jpeg
Processing pexels-photo-5920626.jpeg
Processing pexels-photo-7256898.jpeg
Processing pexels-photo-8488019.jpeg
Processing pexels-photo-5668856.jpeg
Processing pexels-photo-12902928.jpeg
Processing pexels-photo-6232018.jpeg
Processing pexels-photo-3801647.jpeg
Processing pexels-photo-5720979.jpeg
Processing pexels-photo-4483865.jpeg
Processing pexels-photo-5234523.jpeg
Processing pexels-photo-7125542.jpeg
Processing pexels-photo-5025670.jpeg
Processing pexels-photo-6195104.jpeg
Processed pexels-photo-6195104.jpeg: {'image': 'pexels-photo-6195104.jpeg', 'labels': ['Head', 'Face', 'Ear', 'Hands', 'Hands', 'Person', 'Tools', 'Glasses'], 'height': 512, 'width': 512, 'bboxes': [[181.4528, 83.63699199999999, 245.90950400000003, 211.24531199999998], [215.02975999999998, 108.42828800000002, 246.08358400000003, 210.98496], [206.59174400000003, 118.86668800000001, 217.37804799999998, 152.53017599999998], [223.380224, 383.739136, 263.480576, 454.58918400000005]

In [5]:
import torch
from diffusers import StableDiffusionGLIGENPipeline

pipe = StableDiffusionGLIGENPipeline.from_pretrained(
    "masterful/gligen-1-4-inpainting-text-box", variant="fp16", torch_dtype=torch.float16
)
pipe = pipe.to("cuda")

Loading pipeline components...:  43%|████▎     | 3/7 [00:00<00:00,  9.16it/s]/home/joung/r12725056/myenv/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
An error occurred while trying to fetch /home/joung/.cache/huggingface/hub/models--masterful--gligen-1-4-inpainting-text-box/snapshots/d6d957f8d27c40889c0d570a616571a5645c8be3/unet: Error no file named diffusion_pytorch_model.fp16.safetensors found in directory /home/joung/.cache/huggingface/hub/models--masterful--gligen-1-4-inpainting-text-box/snapshots/d6d957f8d27c40889c0d570a616571a5645c8be3/unet.
Defaulting to unsafe serialization. Pass `allow_pickle=False` to raise an error instead.
Loading pipeline components...:  86%|████████▌ | 6/7 [00:01<00:00,  5.32it/s]An error occurred while trying to fetch /home/joung/.cache/huggingface/hub

In [6]:
def normalize_bbox(bbox, img_width, img_height):
    x_min, y_min, x_max, y_max = bbox
    return [
        x_min / img_width,
        y_min / img_height,
        x_max / img_width,
        y_max / img_height,
    ]

In [ ]:
import os
import json
from PIL import Image

# Load the JSON data generated in Stage 1
with open("image_data_blip2-opt-2.7b_200.json", "r") as f:
    enhanced_data = json.load(f)

output_dir = "./generation_200"
os.makedirs(output_dir, exist_ok=True)

for image_name, attributes in enhanced_data.items():
    prompt = attributes["prompt_w_suffix"].strip()
    bboxes = attributes["bboxes"]
    labels = attributes["labels"]
    img_width = attributes["width"]
    img_height = attributes["height"]

    # Normalize bounding boxes
    normalized_bboxes = [normalize_bbox(bbox, img_width, img_height) for bbox in bboxes]
    input_image = Image.open(f"images/{image_name}").convert("RGB")

    # Generate the image
    images = pipe(
        prompt=prompt,
        gligen_phrases=labels,
        gligen_inpaint_image=input_image,
        gligen_boxes=normalized_bboxes,
        gligen_scheduled_sampling_beta=1,
        output_type="pil",
        num_inference_steps=50,
    ).images

    # Save the generated image
    output_path = os.path.join(output_dir, image_name)
    images[0].save(output_path)

/home/joung/r12725056/myenv/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion_gligen/pipeline_stable_diffusion_gligen.py:747: FutureWarning: Accessing config attribute `sample_size` directly via 'AutoencoderKL' object attribute is deprecated. Please access 'sample_size' over 'AutoencoderKL's config object instead, e.g. 'unet.config.sample_size'.
  if gligen_inpaint_image.size != (self.vae.sample_size, self.vae.sample_size):
/home/joung/r12725056/myenv/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion_gligen/pipeline_stable_diffusion_gligen.py:748: FutureWarning: Accessing config attribute `sample_size` directly via 'AutoencoderKL' object attribute is deprecated. Please access 'sample_size' over 'AutoencoderKL's config object instead, e.g. 'unet.config.sample_size'.
  gligen_inpaint_image = self.target_size_center_crop(gligen_inpaint_image, self.vae.sample_size)
100%|██████████| 50/50 [00:03<00:00, 16.09it/s]
Token indices sequence length is longer than t

In [ ]:
resize_images("generation_200", "generation")